
# Simulación de recolección de Cajas con Agentes 

Este Jupyter Notebook implementa una simulación en la que agentes autónomos colaboran para clasificar cajas en pilas de un máximo de 5 cajas cada una. La simulación recopila información sobre el tiempo necesario hasta que todas las cajas están en su lugar y el número total de movimientos realizados por los robots.

En conjunto, estos componentes forman un sistema multiagente *BDI* basado en creencias y deseos, que simula el comportamiento colaborativo de los robots en la clasificación de cajas en un entorno determinado.


![caricatura](robotandbox.jpg)


# Librerias 

Se usaron librerias para realizar la modelacion de los agentes, modelar la Ontologia, realizar los calculos para encontrar el camino mas optimo de los agentes y finalmente para ver la simulacion graficamente

In [1001]:
#Agentes
import agentpy as ap

#Ontologia
from owlready2 import *

#Simulacion
import IPython
import matplotlib.pyplot as plt
from IPython.core.display import display, HTML

#Calculos
import pathfinding as pf        
import itertools
import random
import math

/var/folders/0k/rzljs95518n8gwqkycz_54ww0000gn/T/ipykernel_59378/4175951423.py:10: DeprecationWarning: Importing display from IPython.core.display is deprecated since IPython 7.14, please import from IPython display
  from IPython.core.display import display, HTML


# Ontologia de la simulación

El sistema utiliza una ontología, modelada con Owlready2, para representar entidades y sus relaciones en el mundo simulado. Aquí se definen algunas de las clases y propiedades principales.

Esta ontología permite estructurar la información del mundo simulado de manera más semántica y facilita la actualización de creencias por parte de los agentes.

In [1002]:
# Línea de código para destruir la ontología cada vez que se ejecuta el programa
# Si se omite, puede causar problemas con la información pre guardada
onto.destroy(update_relation=True, update_is_a=True)

# Ruta y nombre de la ontología
onto = get_ontology("file:///content/robot_onto.owl")

# Se abre la ontología
with onto:
    class Entity(Thing):
        pass

    class Robot(Entity):
        pass

    class Box(Entity):
        pass
    
    class Spot(Entity):
        pass

    class Place(Thing):
        pass

    # Propiedad para describir el lugar de una entidad en la cuadrícula
    class is_in_place(ObjectProperty):
        domain = [Entity]
        range = [Place]
        pass

    # Propiedad que especifica la posición de un Lugar
    class at_position(DataProperty, FunctionalProperty):
        domain = [Place]
        range = [str]
        pass

    # Propiedad para describir cuántas cajas puede ver el agente
    class boxes_within_reach(ObjectProperty):
        domain = [Robot]
        range = [int]
        
    # Propiedad para describir cuántos puntos puede ver el agente
    class spots_within_reach(ObjectProperty):
        domain = [Robot]
        range = [int]


# Clase del agente Robot

Representando un agente robot en un sistema basado en la arquitectura BDI. El agente tiene funciones para percibir su entorno, revisar creencias, tomar decisiones basadas en deseos, filtrar objetivos, planificar movimientos, y ejecutar acciones. Utiliza una ontología para instanciar conceptos como la posición del robot, cajas y puntos. El agente busca la caja o punto más cercano como objetivo y planifica movimientos para alcanzarlo. La ejecución del código simula la toma de decisiones y acciones de un robot en un entorno interactivo.


In [1003]:
class RobotAgent(ap.Agent):

    # Funcionalidad relacionada con BDI:

    def see(self, e):
        if self.flag == "cajas":
            tipoDeAgente = 1
        else:
            tipoDeAgente = 2
            # Si lo que quiere es ir hacia una caja, el percepto irá dirigido a agentes de tipo caja
        seeRange = self.model.p.worldSize[0]
        p = [a for a in e.neighbors(self, distance=seeRange) if a.agentType == tipoDeAgente]
        return p

    # Función de revisión de creencias:
    def brf(self, p):
        
        # Destruye creencias anteriores
        for box in self.this_robot.boxes_within_reach:
            destroy_entity(box.is_in_place[0])
            destroy_entity(box)
        destroy_entity(self.this_robot.is_in_place[0])
        
        # Ontológicamente instancia al robot
        currentPos = self.model.boxWorld.positions[self]
        self.this_robot.is_in_place = [Place(at_position=str(currentPos))]
        
        if self.flag == "cajas":
            # Ontológicamente instancia las cajas al alcance
            for c in p:
                theBox = Box(is_in_place=[Place()])
                theBox.is_in_place[0].at_position = str(self.model.boxWorld.positions[c])
                self.this_robot.boxes_within_reach.append(theBox)
        
        elif self.flag == "spots":
            # Ontológicamente instancia los puntos al alcance
            for c in p:
                theSpot = Spot(is_in_place=[Place()])
                theSpot.is_in_place[0].at_position = str(self.model.boxWorld.positions[c])
                self.this_robot.spots_within_reach.append(theSpot)

    # Función de opciones (donde obtiene sus Deseos)
    def options(self):
        """ 
        Retorna las metas disponibles para perseguir.
        Estas se basan en la distancia de cada caja con respecto al robot.
        """
        
        distances = {}
        if self.flag == "cajas":
            # Para cada caja al alcance del robot
            for onto_box in self.this_robot.boxes_within_reach:
                box_pos = eval(onto_box.is_in_place[0].at_position)
                robot_pos = eval(self.this_robot.is_in_place[0].at_position)
                # Calcula la distancia euclidiana:
                d = math.sqrt((box_pos[0] - robot_pos[0]) ** 2 + (box_pos[1] - robot_pos[1]) ** 2)
                # Almacena en un diccionario:
                distances[onto_box] = d
                
        elif self.flag == "spots":
            for onto_spot in self.this_robot.spots_within_reach:
                spot_pos = eval(onto_spot.is_in_place[0].at_position)
                robot_pos = eval(self.this_robot.is_in_place[0].at_position)
                # Calcula la distancia euclidiana:
                d = math.sqrt((spot_pos[0] - robot_pos[0]) ** 2 + (spot_pos[1] - robot_pos[1]) ** 2)
                # Almacena en un diccionario:
                distances[onto_spot] = d
                
        return distances

    # Función de filtrado (donde obtiene la Intención)
    def filter(self):
        """
        Esto devolverá la caja más cercana como objetivo (Intención).
        Se basa en los Deseos del robot.
        """
        # Ordena el diccionario basándose en la distancia de cada caja:
        desires = {x: y for x, y in sorted(self.D.items(), key=lambda item: item[1])}

        # Retorna la primera caja
        if desires:
            return list(desires.items())[0][0]
        else:
            return None

    # Función de planificación (donde el agente crea un plan)
    def plan(self):
        """
        Aquí el robot creará un plan hacia la Intención actual.
        Esto devuelve un plan en forma de una lista de tuplas (x, y).
        Cada paso en el plan es un paso sobre la cuadrícula en las cuatro direcciones principales
        (no diagonal).
        Ejemplo:
            [(1, 0), (0, -1), (-1, 0), (1, 0), etc.]
        """
        if self.I is None:
            if random.randint(0, 1) == 0:
                return [(random.choice([-1, 1]), 0)]
            elif random.randint(0, 1) == 1:
                return [(0, random.choice([-1, 1]))]
            else:
                return [(0, 0)]

        thePlanX = []
        thePlanY = []

        # Obtener la posición objetivo
        boxPos = eval(self.I.is_in_place[0].at_position)
        # Obtener la posición del robot
        robotPos = eval(self.this_robot.is_in_place[0].at_position)
        # Calcular distancias en cada eje
        distance2D = (boxPos[0] - robotPos[0], boxPos[1] - robotPos[1])

        # Crear una lista de pasos atómicos (1 o -1) en el eje X
        for i in range(abs(distance2D[0])):
            val = 1 if distance2D[0] >= 0 else -1
            thePlanX.append(val)

        # Crear una lista de pasos atómicos (1 o -1) en el eje Y
        for j in range(abs(distance2D[1])):
            val = 1 if distance2D[1] >= 0 else -1
            thePlanY.append(val)

        # Crear una lista de tuplas llenas de ceros
        thePlanX = list(zip(thePlanX, [0 for _ in range(len(thePlanX))]))
        thePlanY = list(zip([0 for _ in range(len(thePlanY))], thePlanY))

        # Crear una lista final del plan completo y mezclarla
        # (La parte de mezcla es para tener un agente menos aburrido)
        thePlan = thePlanX + thePlanY
        random.shuffle(thePlan)

        return thePlan

    # El algoritmo BDI principal
    def BDI(self, p):
        """
        Esta función llama a todas las funciones de la arquitectura BDI.
        """
        # Llamando a brf al principio
        self.brf(p)

        # Si el robot alcanzó una meta, entonces actualiza Deseos e Intenciones,
        # y crea un nuevo Plan
        if self.intentionSucceded:
            self.intentionSucceded = False
            self.D = self.options()
            self.I = self.filter()
            self.currentPlan = self.plan()

    # Función para ejecutar acciones
    def execute(self):
        """
        Esta función ejecutará el plan, acción por acción.
        Cada acción es una tupla que tiene un 1 o -1,
        por lo que describen si el agente necesita moverse en una
        dirección u otra.
        """
        # Si el plan no ha terminado
        if len(self.currentPlan) > 0:
            # Entonces obtén la próxima acción
            currentAction = self.currentPlan.pop()
        else:  # Si el plan ha terminado
            # Significa que el robot ha tenido éxito en su tarea actual
            self.intentionSucceded = True
            # Entonces, no hagas nada, hasta el próximo nuevo plan
            currentAction = (0, 0)

        # Ejecuta la acción seleccionada, usando move_by()
        self.model.boxWorld.move_by(self, currentAction)

    # Función de creencias iniciales
    def initBeliefs(self, initPos):
        """
        Esta función llenará el sistema de creencias, instanciando los primeros
        conceptos de la ontología.
        """
        # Instancia inicial de Place
        place = Place(at_position=str(initPos))

        # Instancia inicial de Robot
        self.this_robot = Robot(is_in_place=[place])

    # Función de intenciones iniciales
    def initIntentions(self):
        """
        Esta función proporcionará la primera Intención,
        que en este caso está vacía.
        """
        self.intentionSucceded = True
        self.I = None

    # ====================== Funciones Principales del Agente ===============================================================

    # Configuración
    def setup(self):
        # Identificador del Agente Robot
        self.agentType = 0
        self.firstStep = True
        self.currentPlan = []
        self.flag = "cajas"

    # Paso
    def step(self):
        # Si es el primer paso, entonces inicializa tarde
        if self.firstStep:
            initPos = self.model.boxWorld.positions[self]
            self.initBeliefs(initPos)
            self.initIntentions()
            self.firstStep = False

        # Ejecutar el algoritmo BDI principal
        self.BDI(self.see(self.model.boxWorld))

        # Ejecutar la próxima acción
        self.execute()

    # Actualización
    def update(self):
        pass

    # Fin
    def end(self):
        pass


# Clase del Agente Spot

In [1004]:
# Agente de Recolección

# No hace nada porque no se mueve
class SpotAgent(ap.Agent):

    # Configuración
    def setup(self):
        # Identificador para el Agente de Recolección
        self.agentType = 2

    # Paso
    def step(self):
        pass

    # Actualización
    def update(self):
        pass

    # Fin
    def end(self):
        pass


# Clase del agente Box

In [1005]:
# AGENTE DE CAJA

# No realiza ninguna acción porque no se mueve
class BoxAgent(ap.Agent):

    # Configuración
    def setup(self):
        # Identificador para el Agente de Caja
        self.agentType = 1


    # Paso
    def step(self):
        pass

    # Actualización
    def update(self):
        pass

    # Fin
    def end(self):
        pass


# Modelo del mundo

In [1006]:
# LA SIMULACIÓN

class BoxWorldModel(ap.Model):
    

    # Una función para obtener la cantidad de cajas restantes
    def get_boxes(self):
        return len(self.boxes)

    # Configuración
    def setup(self):

        # Crear agentes robots
        self.robots = ap.AgentList(self, self.p.robotAgents, RobotAgent)

        # Crear agentes cajas
        self.boxes = ap.AgentList(self, self.p.boxAgents, BoxAgent)
        
        # Crear agentes puntos
        self.spots = ap.AgentList(self, self.p.spotsAgents, SpotAgent)

        # Crear el mundo de la cuadrícula
        self.boxWorld = ap.Grid(self, self.p.worldSize, track_empty=True)

        # Agregar agentes a la cuadrícula
        self.boxWorld.add_agents(self.robots, random=True, empty=True)
        self.boxWorld.add_agents(self.boxes, random=True, empty=True)
        self.boxWorld.add_agents(self.spots, random=True, empty=True)


    # Paso
    def step(self):

        # Ejecutar la función de paso de cada agente
        self.robots.step()

        # Verificar si hay una colisión entre un Robot y una Caja
        for robot in self.robots:
            for box in self.boxes:
                if box in self.boxWorld.positions and self.boxWorld.positions[robot] == self.boxWorld.positions[box]:
                    # Si hay una colisión, eliminar la Caja de la cuadrícula y de la simulación
                    self.boxWorld.remove_agents(box)
                    self.boxes.remove(box)
                    robot.flag = "spots"
                    break
        for robot in self.robots:
            for spot in self.spots:
                if spot in self.boxWorld.positions and self.boxWorld.positions[robot] == self.boxWorld.positions[spot]:
                    robot.flag = "cajas"
                    break
        # Si no quedan cajas, terminar la simulación
        if len(self.boxes) <= 0:
            self.stop()

    # Actualización
    def update(self):
        pass

    # Fin
    def end(self):
        pass
    


In [1007]:
#funcion para animar la simulacion
def animation_plot(model, ax):
    agent_type_grid = model.boxWorld.attr_grid('agentType')
    
    ap.gridplot(agent_type_grid, cmap='Accent', ax=ax)
    ax.set_title(f"Simulacion del modelo \n"
                 f"Cajas faltantes: {model.get_boxes()}")
    


In [1008]:
#parametros
#a random variables (0,1)
r = random.random()

#parameters dict
parameters = {
    "robotAgents" : 5,     #Cantidad de robots
    "boxAgents" : 50,      #Cantidad de cajas
    "spotsAgents" : 4,  #Cantidad de lugares de recoleccion
    "worldSize" : (30,30),      #Grid size
    "maxTime" : 1000,          #Max tiempo
    "seed" : 32*r           #seed de variables random 
}


# Simulación

Se utiliza **matplotlib** y **agentpy** para realizar una simulación interactiva. Y se puede observar la animación final en formato HTML de los robots recogiendo las cajas y llevandolas a los puntos a donde se deben apilar. 


In [1009]:

#Create figure (from matplotlib)
fig, ax = plt.subplots()

#Create model
model = BoxWorldModel(parameters)

#Run with animation
animation = ap.animate(model, fig, ax, animation_plot)
#This step may take a while before you can see anything

#Print the final animation
show = IPython.display.HTML(animation.to_jshtml())

show

# Resultados
Se muestra los siguientes resultado de la simulación en base a los parametros establecidos previamente.

1. Tiempo necesario:Tiempo requerido de los robots para recoger la totalidad de las cajas y regresarlos a los lugares de recolección.

2. Número de movimientos: Número de movimientos realizados por todos los robots para terminar la simulación.

In [1010]:
model_info = model.run().info

Completed: 478 steps
Run time: 0:00:29.640026
Simulation finished


In [1011]:

# Convierte la información a HTML con formato
info_html = f"""
<div style="background-color: white; padding: 20px; border: 4px solid #999; border-radius: 5px; text-align: center;">
  <h3 style="margin: 0; color: black; font-size: 18px;">Resultados de la Simulación</h3>
  <ul style="list-style-type: none; padding: 0; color: black; font-size: 16px;">
    <li><strong>Número de movimientos:</strong> {model_info['completed_steps']}</li>
    <li><strong>Tiempo necesario:</strong> {model_info['run_time']}</li>
  </ul>
</div>
"""

# Muestra el HTML en el cuaderno
display(HTML(info_html))